# Histogramming of AGIPD FF data

Author: European XFEL Detector Group, Version: 1.0

Offline Calibration for the AGIPD Detector

In [ ]:
in_folder = "/gpfs/exfel/exp/MID/202030/p900137/proc/" # the folder to read data from, required
out_folder =  "/gpfs/exfel/exp/MID/202030/p900137/scratch/karnem/r0319_0322_0342_v50"  # the folder to output to, required
sequences = [-1] # module to consider, set to -1 for all, range allowed
modules = [5] # module to consider, range allowed
runs = [319] # list of run numbers, required
cells_list = ['range(0,15)'] # list of lists or any python expressions, which can be converted to a list. E.g. 'range(0,15,5)' 'list(range(0,5))+list(range(50,60))'

karabo_id = "MID_DET_AGIPD1M-1" # karabo karabo_id
karabo_da = ['-1']  # a list of data aggregators names, Default [-1] for selecting all data aggregators
receiver_id = "{}CH0" # inset for receiver devices
path_template = 'CORR-R{:04d}-AGIPD{:02d}-S{}.h5' # the template to use to access data
h5path = 'INSTRUMENT/{}/DET/{}:xtdf/image/' # path in the HDF5 file to images

n_bins_adu = 1 # number of bins per ADU
h_range = [-50, 450] # range of the histogram in ADU
n_cells = 202 # total number of memory cells (used to create summary file)

hist_std_tresh = 10 # Threshold for histogram standard deviation
hist_mean_tresh = 15 # Threshold for histogram mean
h_sums_tresh = 100 # Threshold for number of entries in histograms

n_cores_hists = 20 # Number of processes (cores) to create histograms
n_cores_files = 10 # Number of processes (cores) to read files

In [ ]:
import glob
import os
import sys
import traceback
import warnings
from multiprocessing import Pipe, Pool, Process, Queue
from time import perf_counter, sleep, time

import h5py
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import sharedmem
from cal_tools import agipdalgs as calgs
from cal_tools.ana_tools import save_dict_to_hdf5
from XFELDetAna.plotting.heatmap import heatmapPlot

%matplotlib inline
warnings.filterwarnings('ignore')

In [ ]:
if karabo_da[0] != '-1':
    module = int(karabo_da[0][-2:])
else:
    module = modules[0]
    
n_pix = 128*512
h5path = h5path.format(karabo_id, receiver_id)
n_bins = (h_range[1]-h_range[0])*n_bins_adu
print(f"Number of bins: {n_bins}")

In [ ]:
# loop over runs
file_to_read = Queue()
processed = {}
n_files = 0
for irun, run in enumerate(runs):
    
    print(f"Run {run}")
    file_path = f"{in_folder}/r{run:04d}/{path_template}"
    print(f'File path template: {file_path}')

    cells = list(eval(cells_list[irun]))
    if len(cells)>0:
        print(f'List of cells {cells[0]}-{cells[-1]}: {cells}')
    else:
        print('List of cells is empty. Nothing to process.')
        continue

    if sequences[0] == -1:
        fnames = glob.glob(file_path.format(run, module, '*'))
    else:
        fnames = []
        for sequence in sequences:
            fname = file_path.format(run, module, f'{sequence:05d}')
            if os.path.isfile(fname):
                fnames.append(fname)
        
    if not fnames:
        print('No files found.')
        continue
        
    run_sequences = [int(x.split('/')[-1].split('-')[3][1:-3]) for x in fnames]
    print(f"List of sequences: {sorted(run_sequences)}")
    
    processed[run] = sharedmem.empty((max(run_sequences+[1])+1, max(cells+[1])+1), dtype='i4')
    n_files += len(fnames)
    for file in fnames:
        file_to_read.put((file, np.array(cells)))

In [ ]:
# Allocate shared memory for files and histograms
total_hist = sharedmem.empty((n_cells, n_bins, n_pix), dtype='i4')
total_img = sharedmem.empty((n_cells), dtype='i4')
timing = sharedmem.empty((n_cores_files, 3, 2), dtype='f4')

shared_data = {}
for i in range(n_cores_files):
    shared_data[i] = {}
    shared_data[i]['data'] = sharedmem.empty((256*n_cells, 512, 128), dtype='f4')
    shared_data[i]['cellId'] = sharedmem.empty((256*n_cells), dtype='i4')
    shared_data[i]['nImg'] = sharedmem.empty(1, dtype='i4')    
    

In [ ]:
def read_file(file_name, cells, data_path, i_proc):
    """
    Read images and cell Ids from file to the shared memory

    :param file_name: (str) Name of input file including path
    :param cells: (numpy.ndarray, rank=1) array of cells to consider
    :param data_path: (str) Path to data inside of h5 file
    :param i_proc: (int) Index of reader process and corresponding 
        index of shared memory array

    """

    global shared_data
    with h5py.File(file_name, 'r') as f:
        group = f[data_path]

        cell_id = np.squeeze(group['cellId'][()])
        train_id = np.squeeze(group['trainId'][()])
        sel = np.nonzero(np.in1d(cell_id, cells) & (train_id > 0))[0]
        n_img = len(sel)
        shared_data[i_proc]['data'][:n_img] = group['data'][()][sel]
        shared_data[i_proc]['cellId'][:n_img] = group['cellId'][sel]
        shared_data[i_proc]['nImg'][:] = n_img

In [ ]:
def fill_hist(cells, i_proc):
    """
    Calculate histograms and add it to total histograms
    
    :param cells: (numpy.ndarray, rank=1) array of cells to consider
    :param i_proc: (int) Index of reader process and corresponding 
        index of shared memory array

    """

    global shared_data
    n_img = shared_data[i_proc]['nImg'][0]
    for ic, cell in enumerate(cells):
        cell_id = shared_data[i_proc]['cellId'][:n_img]
        cell_sel = np.where((cell_id == cell))

        data = shared_data[i_proc]['data'][:n_img][cell_sel]
        total_hist[cell] += calgs.histogram(data.reshape(data.shape[0], n_pix),
                                              bins=n_bins,
                                              range=h_range)[0].astype(np.int32)

In [ ]:
# Process all files
def file_reader_processor(conn, i_proc, file_to_read, file_to_process):
    """
    Process all files in the file_to_read Queue
    
    Processing of file includes reading file to shared memory and 
    creating of histograms.
    
    :param conn: (pipe) Pipe for communication with manager
    :param i_proc: (int) Index of reader process and corresponding 
        index of shared memory array
    :param file_to_read: (queue) Queue of files to be loaded to shared memory
    :param file_to_process: (queue) Queue of files in shared momery to be processed
        with histogramm_processor
        
    """

    global shared_data
    while not file_to_read.empty():

        file_name, cells = file_to_read.get()
        try:
            ts = perf_counter()
            module_idx = int(file_name.split('/')[-1].split('-')[2][-2:])
            module_name = f"Q{module_idx // 4 + 1}M{module_idx % 4 + 1}"
            run = int(file_name.split('/')[-1].split('-')[1][-4:])
            sequence = int(file_name.split('/')[-1].split('-')[3][1:-3])
            data_path = h5path.format(module_idx)
            
            read_file(file_name, cells, data_path, i_proc)
            t_read = perf_counter()-ts
            
            file_to_process.put((i_proc, cells, run, sequence))
            msg, t_hist = conn.recv()
            t_all = perf_counter()-ts
            
            timing[i_proc][0,0] += t_read
            timing[i_proc][0,1] += t_read**2
            timing[i_proc][1,0] += t_hist
            timing[i_proc][1,1] += t_hist**2
            timing[i_proc][2,0] += t_all
            timing[i_proc][2,1] += t_all**2
            
        except Exception as e:
            err = f"Error: {e}\nError traceback: {traceback.format_exc()}"
            print(f'Error while processing file: \n{file_name}')
            print(err)
            

In [ ]:
def process_manager(conn_proc, conn_hist, file_to_process):
    """
    Manager of reader and histogramming processes
    
    Manager discontinueally monitor a queue.
    If queue is not empty it initiate histogramming of 
    images stored in a shared memory. When images for one file 
    are processed corresponding reader get informed to read next file.
    
    :param conn_proc: (list) List of pipes for communication with readers
    :param conn_hist: (list) List of pipes for communication with histogramm_processors
    :param file_to_process: (queue) Queue of files in shared momery to be processed
        with histogramm_processor
    """
    
    global shared_data
    while True:
        if not file_to_process.empty():
            try:
                info = file_to_process.get()
                if not info:
                    continue
                i_file, cells, run, sequence = info
                ts = perf_counter()
                works = np.array_split(cells, n_cores_hists)

                for i, work in enumerate(works):
                    conn_hist[i].send([work, i_file])
               
                err = ''
                for i in range(n_cores_hists):
                    err += conn_hist[i].recv()
                    
                if err == '':
                    n_img = shared_data[i_file]['nImg'][0]
                    processed[run][sequence, cells] = n_img // len(cells)
                    total_img[cells] += n_img // len(cells)
                else:
                    processed[run][sequence, cells] = 0

            except Exception as e:
                err = f"Error: {e}\nError traceback: {traceback.format_exc()}"
                print(err)
            
            conn_proc[int(i_file)].send(['Done', perf_counter()-ts])
    

In [ ]:
def histogramm_processor(conn):
    """
    Create histograms from images in shared memory
    
    Function discontinuity waiting for a message from 
    process manager. When message arrives histograms are created 
    for requested cells using images from shared memory. After 
    histograms are created message is send back to inform process manager.
    
    :param conn: Pipe to communicate with process_manager
    """
    while True:
        err = ''
        try:
            msg = conn.recv()
            cells, i_proc = msg
            fill_hist(cells, i_proc)
        except Exception as e:
            err = f"Error: {e}\nError traceback: {traceback.format_exc()}"
            print(err)
        conn.send(err)        
    

In [ ]:
# Creare start and join workers
file_to_process = Queue()
file_workers = []
hist_workers = []
manager = None

proc_pipes = []
hist_pipes = []
for i in range(n_cores_files):
    a, b = Pipe()
    proc_pipes.append(b)
    file_workers.append(Process(target=file_reader_processor, 
                                args=(a, i, file_to_read, file_to_process) ) )
    file_workers[i].start()
    
for j in range(n_cores_hists):
    a, b = Pipe()
    hist_pipes.append(b)
    hist_workers.append(Process(target=histogramm_processor, args=(a,) ) )
    hist_workers[j].start()
    
manager = Process(target=process_manager, args=(proc_pipes, hist_pipes, file_to_process) )
manager.start()

ts = perf_counter()
for i in range(n_cores_files):
    file_workers[i].join()

manager.terminate()
manager.join()

for j in range(n_cores_hists):
    hist_workers[j].terminate()
    hist_workers[j].join()

sum_timing = np.sum(timing, axis=0)
ave_timing = sum_timing[:,0] / n_files
std_timing = np.sqrt((sum_timing[:,1] - sum_timing[:,0]**2/n_files)/n_files)
print(f'Processing of {n_files} files finished')
print(f"Total processing time: {perf_counter()-ts:.01f}s")
print(f'Reading time per file: {ave_timing[0]:.01f} +- {std_timing[0]:.02f}s')
print(f'Histogramming time per file: {ave_timing[1]:.01f} +- {std_timing[1]:.02f}s')
print(f'File processing time: {ave_timing[2]:.01f} +- {std_timing[2]:.02f}s')
del shared_data

### Processed files ###

Plots below shows which data have been processed to create histograms.

In [ ]:
for run in processed:
    fig = plt.figure(figsize=(10,5))
    ax = fig.add_subplot(111)

    _ = heatmapPlot(processed[run], add_panels=False, cmap='viridis', use_axis=ax,
                vmin=-1, vmax=256, lut_label='Number of images')
    ax.set_xlabel('Cells', fontsize=14)
    ax.set_ylabel('Sequences', fontsize=14)
    ax.set_title(f"Processed run {run}, module {module}", fontsize=16, fontweight='bold')

In [ ]:
os.makedirs(out_folder, exist_ok=True)
out_name = f'{out_folder}/hists_m{module:02d}_sum.h5'
print(f'Save to file: {out_name}')
save_dict_to_hdf5({'hist': total_hist,
                   'cellId': np.arange(n_cells),
                   'nImages': total_img,
                   'nBins': n_bins,
                   'hRange': np.array(h_range),
                   'runs': processed}, out_name)

In [ ]:
# Perfomr analysis of the data quality
rshist = np.reshape(total_hist, (n_cells, n_bins, 512, 128))

x = np.linspace(h_range[0], h_range[1], n_bins)
mids = 0.5*(x[1:] + x[:-1])

h_sums = np.sum(rshist, axis=1)
hist_norm = rshist / h_sums[:, None, :, :]
hist_mean = np.sum(hist_norm[:, :n_bins-1, ...] *
                   mids[None, :, None, None], axis=1)

hist_std_pix = np.nanstd(hist_mean, axis=(1, 2))
hist_mean_pix = np.nanmean(hist_mean, axis=(1, 2))

h_sum_mean_pix = np.nanmean(h_sums, axis=(1, 2))
h_sum_std_pix = np.nanstd(h_sums, axis=(1, 2))

hist_sqr = (mids[None, :, None, None] - hist_mean[:, None, ...])**2
hist_std = np.sqrt(np.sum(hist_norm[:, :n_bins-1, ...] * hist_sqr, axis=1))

h_out = (h_sums.astype(np.float32) - total_img[:, None, None].astype(
    np.float32))/total_img[:, None, None].astype(np.float32)

## Analysis across all histograms

Mean and standard deviation of the histograms reflect positions of photon peaks. Low value of mean may indicate significant contribution from noise peak. Low standard deviation, comparable with the value of noise may show absence of photon peaks.

Number of entries in histograms expected to be very close to the number of processed images. In case of several processed runs, which covers different cell regions, number of images will be different for different cells. Distribution of histogram entries will have few peaks.

Fraction of outliers expected to be nearly zero for most of the histograms. Large fraction of outliers may significantly distort estimation of position of photon peaks. This likely happen for hot pixels.

In [ ]:
fig = plt.figure(figsize=(10, 5))
ax0 = fig.add_subplot(111)
a = ax0.hist(hist_std.flatten(), bins=100, range=(0,100) )
ax0.plot([hist_std_tresh, hist_std_tresh], [0, np.nanmax(a[0])], linewidth=1.5, color='red' ) 
ax0.set_xlabel('Histogram width [ADU]', fontsize=14)
ax0.set_ylabel('Number of histograms', fontsize=14)
ax0.set_title(f'Module {module}, {hist_std[hist_std<hist_std_tresh].shape[0]} histograms below threshold',
              fontsize=14, fontweight='bold')
ax0.grid()
plt.yscale('log')


fig = plt.figure(figsize=(10, 5))
ax0 = fig.add_subplot(111)
a = ax0.hist(hist_mean.flatten(), bins=100, range=(0,np.nanmax(hist_mean)) )
ax0.plot([hist_mean_tresh, hist_mean_tresh], [0, np.nanmax(a[0])], linewidth=1.5, color='red' ) 
ax0.set_xlabel('Histogram mean [ADU]', fontsize=14)
ax0.set_ylabel('Number of histograms', fontsize=14)
ax0.set_title(f'Module {module}, {hist_mean[hist_mean<hist_mean_tresh].shape[0]} histograms below threshold',
              fontsize=16, fontweight='bold')
ax0.grid()
plt.yscale('log')


fig = plt.figure(figsize=(10, 5))
ax0 = fig.add_subplot(111)
a = ax0.hist(h_sums.flatten(), bins=100, range=(0,np.max(h_sums)) )
ax0.plot([h_sums_tresh, h_sums_tresh], [0, np.nanmax(a[0])], linewidth=1.5, color='red' ) 
ax0.set_xlabel('Number of entries in histogram', fontsize=14)
ax0.set_ylabel('Number of histograms', fontsize=14)
ax0.set_title(f'Module {module}, {h_sums[h_sums<h_sums_tresh].shape[0]} histograms below threshold',
              fontsize=16, fontweight='bold')
ax0.grid()
plt.yscale('log')

fig = plt.figure(figsize=(10, 5))
ax0 = fig.add_subplot(111)
a = ax0.hist(h_out.flatten(), bins=100, range=(-1, 0))
ax0.set_xlabel('Fraction of outliers in histograms', fontsize=14)
ax0.set_ylabel('Number of histograms', fontsize=14)
ax0.set_title(f'Module {module}', fontsize=16, fontweight='bold')
ax0.grid()
plt.yscale('log')

## Analysis across cells

Behavior of histograms across cells is shown below by presenting values averaged across pixels. Mean value of the histogram have quite visible deviation across cells. This deviation may be driven either by the position of photon peak or by different (across cells/pulses) intensity of the beam. Error-band shows deviation of the mean value across pixels.

Number of entries per histogram averaged across pixels should nearly coincides with number of processed images for given cell. Both lines expected to be flat in case of processing on only one dataset (one run). Zero number of images suggests, that corresponding region of cells was not covered by dataset or not processed.

Histogram range is chosen to cover noise peak and all visible photon peaks. Significant number of outliers may make photon peak analysis impossible.

In [ ]:
x = np.linspace(0, n_cells, n_cells)
fig = plt.figure(figsize=(10, 12))

ax0 = fig.add_subplot(211)
ax0.plot(x, hist_mean_pix, 'k', color='#3F7F4C')
ax0.fill_between(x, hist_mean_pix-hist_std_pix, hist_mean_pix+hist_std_pix,
                 alpha=0.6, edgecolor='#3F7F4C', facecolor='#7EFF99',
                 linewidth=1, linestyle='dashdot', antialiased=True,
                 label=" mean value $ \pm $ std ")

ax0.set_xlabel('Cell', fontsize=14)
ax0.set_ylabel('Mean over pixels [ADU]', fontsize=14)
ax0.set_title(f'Module {module}', fontsize=16, fontweight='bold')
ax0.grid()
_ = ax0.legend()

ax1 = fig.add_subplot(212)
ax1.plot(x, h_sum_mean_pix, 'k', color='#3F7F4C', label='# entries per histograms')
ax1.plot(x, total_img, 'k', color='red',  linestyle='dashdot', label='# processed images')



ax1.set_xlabel('Cell', fontsize=14)
ax1.set_ylabel('# entries averaged across pixels', fontsize=14)
ax1.set_title(f'Module {module}', fontsize=16, fontweight='bold')
_ = ax1.legend()


fig = plt.figure(figsize=(10, 6))
ax0 = fig.add_subplot(111)
ax0.plot(x, 1-h_sum_mean_pix/total_img, 'k', color='#3F7F4C')


ax0.set_xlabel('Cell', fontsize=14)
ax0.set_ylabel('Average fraction of outliers', fontsize=14)
ax0.set_title(f'Module {module}', fontsize=16, fontweight='bold')
ax0.grid()

## Single pixel overview

Plot below shows histograms for single pixel and all memory cells. It should contain noise peak and well pronounced one or few photon peaks. Estimation of the photon peak position requires to have comparable hight of the noise and first photon peak.

In [ ]:
# Plot for single pixel and all memory cells.
xpix= 23
ypix= 44

x = np.arange(h_range[0],h_range[1] , 1)
n,_ = rshist[:,:,xpix,ypix].shape

colors = mpl.cm.rainbow(np.linspace(0, 1, n))


fig = plt.figure(figsize=(10,5))
fig.suptitle(f'Module {module} ', fontsize=14, fontweight='bold')

ax = fig.add_subplot(111)
fig.subplots_adjust(top=0.85)
ax.set_title(f'single pixel [{xpix},{ypix}], all ({n_cells}) memory cells')

ax.set_xlabel('Signal [ADU]')
ax.set_ylabel('Counts')
ax.set_xlim(-50,300)
for color, y in zip(colors, rshist[:,:,xpix,ypix]):
    ax.plot(x, y, color=color,linewidth=0.2)
plt.grid()  
plt.show()